In [1]:
import numpy as np
import plotly.graph_objects as go
import scipy as sp
from scipy.optimize import fsolve
import matplotlib.pyplot as plt

## problem 6

In [10]:
beta = 0.89305
re   = 7.1053
De   = 4.456 * 1e-4
b    = 0
E    = 0.006
initial_guess = 5
dr = 1e-5

def Vmorse(r : np.double):
    return De * (np.exp(-2. * beta * (r - re)) - 2 * np.exp(-beta * (r - re)))

def term(r):
    return 1 - b * b / (r * r) - Vmorse(r) / E

rmin = fsolve(term, 5)
print("founded zero at {}".format(rmin))
print("Debug  : {}".format(fsolve(term, rmin)))
print("Value at that point : {} ".format(term(rmin)))
print("Values at rmin-dr : {}       rmin+dr : {} ".format(term(rmin-dr), term(rmin + dr)))

p6_x = np.linspace(4, 10, 10000)
p6_y = term(p6_x)


fig = go.Figure()
fig.add_trace(go.Scatter(x=p6_x, y=p6_y, mode="lines", name="morse"))
fig.show()

founded zero at [5.34806306]
Debug  : [5.34806306]
Value at that point : [-6.66133815e-16] 
Values at rmin-dr : [-2.42326941e-05]       rmin+dr : [2.42322044e-05] 


## problem 7

$$
    \theta = \pi - 2 b \int^{\infty}_{r_{min}} r^{-2} [1 - \frac{b^{2}}{r^{2}} - \frac{V(r)}{E}]^{-0.5} dr
$$

In [3]:
sigma = 1


def V7(r : np.double):
    if r > sigma:
        return 0
    return float("inf")


$$ b = x \sigma $$
$$ r = \rho \sigma $$
$$ dr = \rho d \sigma $$
$$ x \leq 1 $$
$$ \sigma = r_{min} $$
Limits  : 
$ r = \sigma $ to $ r = \infty $ <br>
$$ r = \rho \sigma = \sigma $$
$$ \rho = 1 $$

Substituting to :
$$
    \theta = \pi - 2 b \int^{\infty}_{r_{min}} r^{-2} [1 - \frac{b^{2}}{r^{2}} - \frac{V(r)}{E}]^{-0.5} dr
$$
Results in

$$
    \theta = \pi - 2 x \sigma \int^{\infty}_{r_{min}} \frac{1}{(\rho \sigma)^{2} } [1 - \frac{(x\sigma)^{2}}{(\rho \sigma)^2}]^{-0.5} \rho d \sigma
$$ <br>
$$
    \theta = \pi - 2 x \sigma \int^{\infty}_{r_{min}} \frac{1}{(\rho \sigma)^{2} } [1 - \frac{(x\sigma)^{2}}{(\rho \sigma)^2}]^{-0.5} \rho d \sigma
$$
$$
    \theta = \pi - 2 x \sigma \int^{\infty}_{r_{min}} \frac{1}{(\rho \sigma)^{2} } [1 - \frac{(x)^{2}}{(\rho )^2}]^{-0.5} \rho d \sigma
$$
$$
    \theta = \pi - 2 x \sigma \int^{\infty}_{r_{min}} \frac{1}{(\rho \sigma)^{2} } [\frac{ \rho^{2} - x^{2}}{(\rho )^2}]^{-0.5} \rho d \sigma
$$
$$
    \theta = \pi - 2 x \int^{\infty}_{1} [\frac{1 }{\rho \sqrt{\rho^{2} - x^{2}}}] d \sigma
$$
Evaluate algebraically the integral above using sympy

In [4]:
from sympy import *
y = Symbol('y')
x = Symbol('x')
integrate(1 / (y * sqrt(y * y - x*x)), y)

Piecewise((I*acosh(x/y)/x, Abs(x**2/y**2) > 1), (-asin(x/y)/x, True))

Plugging in the limits will result in : 
$$ \theta_{hs}(b) = \pi - 2x \frac{asin(|x|)}{x} $$
$$ \theta_{hs}(b) = \pi - 2 asin(|x|) $$
$$ \theta_{hs}(b) = \pi - 2 asin(|\frac{b}{\sigma}|) $$

In [5]:
sigma = 1
def prob7(b):
    return np.pi - 2 * np.arcsin(np.abs(b / sigma))

x = np.linspace(0, sigma, 10000)

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=prob7(x) * 180 / np.pi, mode="lines", name="morse"))
fig.show()

## problem 8

In [11]:
from scipy.integrate import quad, simps, trapz

b = None
E = 0.002
V = Vmorse



def integrand(r):
    global b
    return np.power(r, -2) * np.power(1 - b * b / (r * r) - V(r) / E, -0.5)

def integrate(b_, rmin, rmax):
    global b
    b = b_
    return np.pi - 2 * b * quad(integrand, rmin, rmax)[0]

def solveForEnergy(E_, b_start=0, b_end=15, points=5000):
    global E
    global b
    E = E_
    b8 = np.linspace(b_start, b_end, points)
    y8 = []
    for b in b8:
        rmin = fsolve(term, 5)
        y8.append(integrate(b, rmin, 3000))
    return b8, np.array(y8)
    
b8, y8 = solveForEnergy(0.002)
b8_2, y8_2 = solveForEnergy(0.006)
b8_3, y8_3 = solveForEnergy(0.00075)
b8_4, y8_4 = solveForEnergy(0.001)
b8_5, y8_5 = solveForEnergy(0.02)

fig = go.Figure()
fig.add_trace(go.Scatter(x=b8_5, y=y8_5 * 180 / np.pi, mode="lines", name="E=0.02"))
fig.add_trace(go.Scatter(x=b8, y=y8 * 180 / np.pi, mode="lines", name="E=0.002"))
fig.add_trace(go.Scatter(x=b8_2, y=y8_2 * 180 / np.pi, mode="lines",name="E=0.006"))
fig.add_trace(go.Scatter(x=b8_4, y=y8_4 * 180 / np.pi, mode="lines",name="E=0.001"))
fig.add_trace(go.Scatter(x=b8_3, y=y8_3 * 180 / np.pi, mode="lines",name="E=0.00075"))
fig.show()

In [12]:
b8_6, y8_6 = solveForEnergy(0.75)
b8_7, y8_7 = solveForEnergy(0.4)
b8_8, y8_8 = solveForEnergy(0.3)


fig = go.Figure()
fig.add_trace(go.Scatter(x=b8_6, y=y8_6 * 180 / np.pi, mode="lines", name="E=0.75"))
fig.add_trace(go.Scatter(x=b8_7, y=y8_7 * 180 / np.pi, mode="lines", name="E=0.4"))
fig.add_trace(go.Scatter(x=b8_8, y=y8_8 * 180 / np.pi, mode="lines", name="E=0.3"))
fig.show()

C:\Users\levus\AppData\Local\Continuum\anaconda3\lib\site-packages\scipy\optimize\minpack.py:162: RuntimeWarning:

The iteration is not making good progress, as measured by the 
  improvement from the last ten iterations.



## Problem 9

In [15]:
def p9(beta, theta):
    db = beta[1] - beta[0]
    
    dtheta = np.gradient(theta, db)
    rainbowAngle = np.abs(np.min(dtheta))
    
    dang = rainbowAngle / 30.
    
    angl = np.arange(1, rainbowAngle, dang)
    angg = np.arange(rainbowAngle, 180, dang)
    
    return rainbowAngle
    
bet, thet = b8, y8 * 180 / np.pi
print(p9(bet, thet))

36.53140338435131
